# Multidimensional Nonlinear Problems

## Introduction

* Consider the following 2 equations:
$$f(x,y) = 0$$
$$g(x,y) = 0$$
$f(x,y)$ is a surface (3D).  So is $g(x,y)$.  
    * They will intersect in a curve. 
<img src="https://ignite.byu.edu/che541/lectures/figs/l10f1.png" width="400">

* The solution is where this curve intersects the f=g=0 plane.  
    * This will happen at specific points.  
        * These are the solutions.
    * There may be more than one. 

* You could also consider that the $f(x,y)$ surface will intersect the $z=0$ plane in a curve.  $g(x,y)$ likewise.  The solutions will be where these two curves in the $z=0$ plane intersect. 
* This is more complex than the 1D situation with $f(x)=0$.
* Many methods that work well for 1D are difficult to extend to multi-D problems.  But Newton's method extends easily.

## Newtons Method

* If we can't solve our problem, solve an easier problem.
    * In 1D, we made an initial guess, then approximated $f(x)$ as being linear around the guess, then we solved the linear problem to get an updated guess.
    * We used a truncated Taylor series representation of $f(x)$ about point $x_0$:
    $$f(x)\approx f(x_0) + f^{\prime}(x_0)(x-x_0)$$
<img src="https://ignite.byu.edu/che541/lectures/figs/l10f2.png" width="300">   

* We'll do the analogous thing in 2-D:
    * Make an initial guess for $x$ and $y$.
    * Approximate $f(x,y)$ and $g(x,y)$ as tangent planes at the guess.
    * Find the intersection of the tangent planes with the $y=0$ plane.  The intersection of the tangent planes will be a line, and location of the intersection of that line with $y=0$ will be the solution.

### Multi-dimensional Newton's Method

* Write the 2-D Taylor series approximations for $f(x,y)$ and $g(x,y)$ keeping just the linear terms:
$$f(x,y) \approx f(x_0,y_0) + \left.\frac{\partial f}{\partial x}\right|_{x_0,y_0}\delta x + \left.\frac{\partial f}{\partial y}\right|_{x_0,y_0}\delta y$$ 
$$g(x,y) \approx g(x_0,y_0) + \left.\frac{\partial g}{\partial x}\right|_{x_0,y_0}\delta x + \left.\frac{\partial g}{\partial y}\right|_{x_0,y_0}\delta y,$$
where $\delta x = (x-x_0)$, and similar for $\delta y$.

* Now, on the left, $$f(x,y)=g(x,y)=0.$$  In matrix form we have:
$$
\left(\begin{array}{c}
0 \\
0
\end{array}\right) =
\left(\begin{array}{c}
f(x_0,y_0) \\
g(x_0,y_0)
\end{array}\right) +
\left[\begin{array}{cc}
\frac{\partial f}{\partial x} &\frac{\partial f}{\partial y} \\
\frac{\partial g}{\partial x} &\frac{\partial g}{\partial y} 
\end{array}\right]
\left(\begin{array}{c}
\delta x \\
\delta y
\end{array}\right) 
$$
Or, rearranging:
$$[J](\boldsymbol{\delta x}) = -(\boldsymbol{f}(\boldsymbol{x}_0)),$$
where bold symbols denote vector quantities: the elements of $\boldsymbol{\delta x}$ are $\delta x$ and $\delta y$, etc.



* Note, for multi-D problems, its more convenient to use $f_1$, $f_2$, etc., instead of $f$, $g$, etc.  (so we don't run out of symbols).  Likewise, we have $x_1$, $x_2$, etc., rather than $x$, $y$, etc.
* Solve for $\boldsymbol{\delta x}$ as 
$$ \boldsymbol{\delta x} = -J^{-1}\boldsymbol{f}(\boldsymbol{x}_0).$$

* J is the Jacobian matrix, the matrix of partial derivatives.
    * In general, the elements $i$, $j$ (row, column) of $J$ are $J_{i,j} = \partial f_i/\partial x_j.$
    * $J$ can be expensive to compute, so it is often reused for a certain number of Newton iterations.
* Once we have $\boldsymbol{\delta x}$ we can solve for $\boldsymbol{x}_{new} = \boldsymbol{x}_{old} + \boldsymbol{\delta x}.$ 
* *<font color='blue'>This is another example of numerical methods reducing to solution of a system of linear equations.</font>*

### Implementation

* Recall, in 1D, we needed three functions:
    1. The Newton routine that does the Newton steps.
    2. A function for $f(x)$.
    3. A function for $df/dx$.
* We have the same thing in multi-dimensional cases:
    1. The Newton routine that does the Newton steps.  This will perform the $\boldsymbol{\delta x} = -J^{-1}\boldsymbol{f}(\boldsymbol{x}_0)$ inversion, compute $\mathbf{x}$ from $\boldsymbol{\delta x}$, perform convergence checks, etc.
    2. A function that takes vector $x$ and returns vector $\mathbf{f}(\mathbf{x})$.
    3. A function that takes $x$ (and ideally $\mathbf{f}(\mathbf{x})$ too) and returns matrix $J$.

### 1-D Newton

In [5]:
function newton1D(x, f, dfdx, tol, maxit=100)
    
    for it in 1:maxit
        xnew = x - f(x)/dfdx(x)            
        if abs((xnew-x)/xnew) <= tol
            return xnew,it+1
        end
        x = xnew
        if it == maxit
            println("Warning, no convergence in $maxit iterations")
            return xnew,it+1
        end
    end
end;

### Multi-Dimensional Newton

In [8]:
import LinearAlgebra: norm

function multiNewt(f, Jac, x, tol, maxit=100)
    
    for it in 1:maxit
        fvec = f(x)
        J    = Jac(x)
        xnew = x - J\fvec            
        if norm(xnew-x)/norm(xnew) <= tol
            return xnew,it+1
        end
        x = xnew
        if it == maxit
            println("Warning, no convergence in $maxit iterations")
            return xnew,it+1
        end
    end
end;

Solve:

$$f(x,y) = x^2 + y^2 - 3 = 0,$$

$$g(x,y) = 2y - x^2 = 0.$$

In [15]:
fg(x) = [ x[1]^2 + x[2]^2 - 3,  
          2*x[2] - x[1]^2 ]

Jac(x) = [ 2*x[1]  2*x[2]; 
          -2*x[1]     2.0  ];

In [19]:
x0 = [10, 10]

x_solution,nit = multiNewt(fg, Jac, x0, 1.E-6)
println("solution: $x_solution")
println("f(x):     $fg(x_solution)")

solution: [1.414213562373095, 1.0]
f(x):     fg(x_solution)


KeyError: KeyError: key "debug_request" not found

## Numerical derivatives
If the derivative of $f(x)$ is unknown, or inconvenient, a numerical derivative can be used:

$$f^{\prime}(x)\approx\frac{f(x+\Delta x)-f(x)}{\Delta x},$$

$$\Delta x = \sqrt{\epsilon_{mach}}\;|x| = 10^{-8}|x|.$$

The second expression is an optimized value for $\Delta x$. See N.R. section 5.7, p. 229, 3rd edition for details.
* Here, $x$ is your current estimate for the solution.

### Details
* The following is from Numerical Recipes 3rd edition.
* Find the optimal $\Delta x$ by balancing truncation error and roundoff error.
* The truncation error is given by $$\epsilon_t = \frac{1}{2}\Delta xf^{\prime\prime}$$
* The roundoff error in evaluating $f^\prime$ is given by $$\epsilon_r = \epsilon_{mach}\frac{f}{\Delta x}$$
    * That is, we are doing operations on terms of magnitude $f/\Delta x$, so the roundoff error occurs with magnitude $\epsilon_{mach}$ multiplied by this magnitude.
    * (In double precision, we are scaling the 16th decimal.)
* We sum the roundoff and truncation error, take the derivative with respect to $\Delta x$, set this equal to zero, and solve for $\Delta x$ to give

$$\Delta x  = \sqrt{\frac{2\epsilon_{mach}f}{f^{\prime\prime}}} \sim \sqrt{\frac{\epsilon_{mach}f}{f^{\prime\prime}}}$$

* Finally, $f/f^{\prime\prime}$ is taken as a curvature scale, which has *units* of $x^2$, and nominally scales as $x^2$, so is taken as $x^2$, except at or near $x=0$.
$$\Delta x \sim x\sqrt{\epsilon_{mach}}$$

## Summary of nonlinear solution methods

| Method | Notes | Convergence | Order | Comments |
|--------|-------|-------------|:-----:|----------|
| Bisection | simple, brackets root, slow | robust | 1 | good for finding a root, refine with an open method|
| Regula Falsi | brackets root, linear interpolation | robust | >1 | faster than bisection|
| Fixed Point  | $x=g(x)$, no unique form, but easy  | inconsistent | 1 | easy to use but unreliable |
| Newton's | analytic or numerical derivatives | converges close to root | 2 | widely used, needs a good starting point|
| secant | Like Regula Falsi, use last 2 points| may not converge | 1.62 | recommended when no analytic derivative |
| <font color='grey'> *Muller's* </font>| <font color='grey'>*like Secant, but 3 pt interpolant* </font> | <font color='grey'> *may not converge* </font> | <font color='grey'> *1.84* </font> | <font color='grey'> *not as common, use Newton or Secant* </font> |
| <font color='grey'> *Brents's* </font>| <font color='grey'>*combo of bracketing, bisection, interpolation* </font> | <font color='grey'> *robust* </font> | <font color='grey'> *--* </font> | <font color='grey'> *recommended by N.R.* </font> |